Load two surfaces $f_1$ and $f_2$ of size $3*N_{\phi}*N_{\theta}$, where $N_\phi$ denotes the number of discrete polar angle $\phi\in[0,\pi]$ and $N_\theta$ denotes the number of discrete azimuthal angle $\theta\in[0,2\pi]$.

To use the code, $N_{\theta}$ must be **odd** and the matrix representation of each surface should satisfy $f[:, 0, :] = f[:, 0, 0]$, $f[:, -1, :] = f[:, -1, 0]$ and $f[:, :, 0] = f[:, :, -1]$, i.e., $f(0, \theta) = f(0, 0)$, $f(\pi, \theta) = f(\pi, 0)$ and $f(\phi, 0) = f(\phi, 2\pi)$.

In [1]:
import scipy.io as sio
from ShapePackages.ComputeGeoShape import *
from ShapePackages.Initialization_Diffs_SRNF import initialize_over_diffs_main_SRNF

# Example 

mat_f= sio.loadmat('ShapeData/example_50_99.mat')
f1 = torch.from_numpy(mat_f['f1']).float()
f2 = torch.from_numpy(mat_f['f2']).float()

Initialize the first boundary surface using SRNFs

In [2]:
lam = 2 # the maximal degree of spherical harmonics to align the first surface 
MaxIte = 50  # the maximum number of iterations in the optimization process

f, Energyrepa1, f1_gamma1, ESO31, f1_barh1, EIco1 = initialize_over_diffs_main_SRNF(f1, f2, lam, MaxIte)

Calculate a geodesic in the space of unparametrized surfaces

In [3]:
%%time

T = 7
a, b, c, d = 1, 1/2, 1, 0

opts = {'Cmetric': (a, b, c, d),  # choices of the split metric
        'Tpts': T,  # the number of the time points 
        'MaxDegHarmSurf': 7,  # the maximal degree of spherical harmonics for the space of parametrized surfaces
        'MaxDegVecFS2': 7,  # the maximal degree of spherical harmonics for the tangent vector fields on S2
#         'method': 'combined',  # the method to calculate geodesics: 'split (default)', 'combined'
#         'multires': True, # only for the split method
        'maxiter': (10,20) # (N0, N1) N0: the maximal number of iterations for the whole optimization process
                           #          N1: the maximal number of iterations for each of the first N0-1 optimizations
                           #        In the last optimization process 100 maximum iterations is used. The whole maximal
                           #        number of iterations will be (N0-1)*N1 + 100  
       }  

geo_f, EnergyAll0 = compute_geodesic_shape_main(f, f2, **opts)

Wall time: 3min 2s


In [4]:
from ShapePackages.OneFormRieMetric import length_func_surf_Imm
length_func_surf_Imm(geo_f, a, b, c, d)

tensor(1.3819)

In [5]:
print('The number of iterations in the optimization process is', len(EnergyAll0),'and the final energy is', EnergyAll0[-1])

The number of iterations in the optimization process is 178 and the final energy is 1.9118156433105469


In [6]:
# plot the energy 
import matplotlib.pyplot as plt
plt.plot(EnergyAll0)
plt.show()

<Figure size 640x480 with 1 Axes>

In [7]:
# plot the geodesic

idty = get_idty_S2(*f1.shape[-2:])

from mayavi import mlab
Gx, Gy = np.gradient(idty[2]) # gradients with respect to x and y
Grad = (Gx**2+Gy**2)**.5  # gradient magnitude  PHI, THETA
w = Grad/Grad.max()  

%gui qt

mlab.init_notebook('x3d',1000,500) # png & x3d
mlab.figure(1, size=(100,70), fgcolor=(1, 1, 1), bgcolor=(0.5, 0.5, 0.5))
mlab.clf()

# plot the geodesic
for i in range(T):
    s0 = mlab.mesh(geo_f[i, 0].numpy()+2*i, geo_f[i, 1].numpy(), geo_f[i, 2].numpy()-2,representation='wireframe',scalars=w)

mlab.view(azimuth=270, elevation=90) 
mlab.show()
s0

Notebook initialized with x3d backend.
